In [1]:
import numpy as np
import pandas as pd
import os
import quandl as ql
import matplotlib.pyplot as plt
from datetime import datetime
import plotly.express as px
import panel as pn
from ipywidgets import interact, fixed
import ipywidgets as widgets
import hvplot.pandas 
pn.extension("plotly")


Bad key "text.kerning_factor" on line 4 in
C:\Users\sinth\anaconda3\envs\pyvizenv\lib\site-packages\matplotlib\mpl-data\stylelib\_classic_test_patch.mplstyle.
You probably need to get an updated matplotlibrc file from
http://github.com/matplotlib/matplotlib/blob/master/matplotlibrc.template
or from the matplotlib source distribution


In [2]:
from dotenv import load_dotenv
load_dotenv()

True

In [3]:
QUANDL_KEY = os.getenv("QUANDL_KEY")

In [4]:
ql.ApiConfig.api_key = QUANDL_KEY

In [5]:
def cleanData(df, asset_class, security):
    cleaned_df = df[['Noncommercial Long', 'Noncommercial Short']]
    cleaned_df['Noncommercial Long Percent'] = cleaned_df['Noncommercial Long'] /(cleaned_df['Noncommercial Long'] + cleaned_df['Noncommercial Short'])
    cleaned_df['Noncommercial Short Percent'] = cleaned_df['Noncommercial Short'] /(cleaned_df['Noncommercial Long'] + cleaned_df['Noncommercial Short'])
    cleaned_df['Net Noncomercial'] = cleaned_df['Noncommercial Long'] - cleaned_df['Noncommercial Short']
    cleaned_df['Asset Class'] = asset_class
    cleaned_df['Security'] = security
    return cleaned_df[['Asset Class','Security','Noncommercial Long Percent', 'Noncommercial Short Percent', 'Net Noncomercial']]

In [6]:
def get_stats(df, window):
    roling_df = df.loc[:,'Net Noncomercial'].rolling(window=window)
    mean_rolling = roling_df.mean().shift(1)
    std_rolling = roling_df.std(ddof=0).shift(1)
    z_score = (df.loc[:,'Net Noncomercial']-mean_rolling)/std_rolling
    mean = df.loc[:,'Net Noncomercial'].mean()
    std = df.loc[:,'Net Noncomercial'].std(ddof=0)
    df['Mean'] = mean
    df['Std'] = std
    df['Z Score'] = z_score
    return df.dropna()

In [7]:
def createMarkers(df, abs_threshold):
    stats_df = df.reset_index()
    start_period = False
    ranges = []
    for date, z_score in zip(stats_df['Date'], stats_df['Z Score']):
        if abs(z_score) > abs_threshold:
            x_0 = date.to_pydatetime()
            start_period = True
        elif abs(z_score) < abs_threshold and start_period == True:
            x_1 = date.to_pydatetime()
            start_period = False
            ranges.append([x_0, x_1])
    return ranges

In [29]:
def createPlot(qndl_code, asset_class, sec_type, interval, abs_threshold):
    data = ql.get(qndl_code)
    data_cleaned = cleanData(data, asset_class, sec_type)
    stats_df = get_stats(data_cleaned, interval)
    new_marker = createMarkers(stats_df, abs_threshold)
    y_0 = stats_df['Net Noncomercial'].min()
    y_1 = stats_df['Net Noncomercial'].max()
    graph = px.line(stats_df, y='Net Noncomercial', title = sec_type )
    for x_0, x_1 in new_marker:
        graph.add_shape(
                dict(
                    type="rect",
                    x0=x_0,
                    x1=x_1,
                    y0 = y_0,
                    y1 = y_1,
                    line=dict(
                        color="red",
                        width=3,
                    ),
                    fillcolor="red",
                    opacity=0.5,
        ))
    return graph

In [9]:
securities_to_analyze = [
    {
        'qndl_code':'CFTC/084691_FO_L_ALL',
        'asset_class':'Commodity',
        'sec_type': 'Silver'
    },
    {
        'qndl_code':'CFTC/088691_FO_L_ALL',
        'asset_class':'Commodity',
        'sec_type': 'Gold'
    },
    
    {
        'qndl_code':'CFTC/085692_FO_L_ALL',
        'asset_class':'Commodity',
        'sec_type': 'Copper'
    },
    {
        'qndl_code':'CFTC/209742_FO_L_ALL',
        'asset_class':'Stock',
        'sec_type': 'Nasdaq'
    },
    {
        'qndl_code':'CFTC/099741_FO_L_ALL',
        'asset_class':'Currency',
        'sec_type': 'EURO'
    },
    {
        'qndl_code':'CFTC/090741_FO_L_ALL',
        'asset_class':'Currency',
        'sec_type': 'CAD'
    },
    {
        'qndl_code':'CFTC/098662_FO_L_ALL',
        'asset_class':'Currency',
        'sec_type': 'USD'
    },
    
]

In [31]:
interval = 52
abs_threshold  = 1.5
column = pn.Column('#Market Consensus vs Zscore')
for security in securities_to_analyze:
    graph = createPlot(security['qndl_code'], security['asset_class'], security['sec_type'], interval, abs_threshold)
    column.append(graph)
column


C:\Users\sinth\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy

C:\Users\sinth\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy

C:\Users\sinth\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata

Column
    [0] Markdown(str)
    [1] Plotly(Figure)
    [2] Plotly(Figure)
    [3] Plotly(Figure)
    [4] Plotly(Figure)
    [5] Plotly(Figure)
    [6] Plotly(Figure)
    [7] Plotly(Figure)

In [12]:
def getDataFrames(qndl_code):
    data = ql.get(qndl_code)
    data_cleaned = data[['Noncommercial Long', 'Noncommercial Short']]
    data_cleaned['Net Noncommercial'] = data_cleaned['Noncommercial Long'] - data_cleaned['Noncommercial Short']
    return data_cleaned

In [13]:
combine_df = pd.DataFrame()
for security in securities_to_analyze:
    df = getDataFrames(security['qndl_code'])
    asset_name = security['sec_type']
    combine_df[f'{asset_name} Net Noncommercial'] = df['Net Noncommercial']

combine_df = combine_df.dropna().copy()
grouped_df = combine_df.groupby(combine_df.index.year).mean()

C:\Users\sinth\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy



In [14]:
column2 = pn.Column('# Correlation Between Securities')
column2.append(px.parallel_coordinates(grouped_df))
column2

Column
    [0] Markdown(str)
    [1] Plotly(Figure)

In [19]:
column3 = pn.Column('#Position Overview')
for security in securities_to_analyze:
    df = getDataFrames(security['qndl_code'])
    cleaned_df = cleanData(df, security['asset_class'], security['sec_type'])
    cleaned_df = cleaned_df.reset_index()
    graph = cleaned_df.hvplot.area(x = 'Date',  y=['Noncommercial Long Percent','Noncommercial Short Percent' ], label='% of Long Positions')
    column3.append(graph)

C:\Users\sinth\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy

C:\Users\sinth\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy

C:\Users\sinth\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata

In [20]:
column3

Column
    [0] Markdown(str)
    [1] HoloViews(NdOverlay)
    [2] HoloViews(NdOverlay)
    [3] HoloViews(NdOverlay)
    [4] HoloViews(NdOverlay)
    [5] HoloViews(NdOverlay)
    [6] HoloViews(NdOverlay)
    [7] HoloViews(NdOverlay)